In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
import pandas as pd
import matplotlib.pyplot as plt          # plotting
import numpy as np                       # dense matrices
from scipy.sparse import csr_matrix      # sparse matrices
%matplotlib inline
import cv2


In [ ]:
import numpy as np
from skimage import feature
from skimage import io
from skimage.color import rgb2gray
import numpy as np
from skimage.feature import local_binary_pattern
from skimage import io, color
import numpy as np
import pandas as pd
import cv2

dirr1= r"/content/drive/MyDrive/Main_data_set_x_ray_IMG/Furier_transform/pneumonia_2"
 #### source folder

csv=r"/content/drive/MyDrive/XRayRadioPathyDataset/GNN_Features/old_pneumonia - Sheet1.csv"
 ### csv save path
### must change csv path

c= 2 ### c=class 1=0 or class 2=1

#####################################################################################################

j=0
df1 = pd.DataFrame(columns=['Class', 'Perimeter', 'Area', 'Circularity', 'aspect_ratio', 'Extent', 'Solidity','Rect','Rect_area','num_vessels','contrast','dissimilarity','homogeneity','energy','correlation','glrlm','mean_density','std_density','lung_volume','hist','uniformity'])
#df1 = pd.DataFrame(columns=['class', 'wb_ratio'])
import os
onlyfiles = next(os.walk(dirr1))[2] #dir is your directory path as string
#print(len(onlyfiles))

for i in os.listdir(dirr1):
    path = os.path.join(dirr1,i)
    img = cv2.imread(path)
    print('working on img ',i)
    gray = cv2.cvtColor(img, cv2.COLOR_BGR2GRAY)




# solidity, perimeter,circularity
    # Apply a Gaussian blur to reduce noise

    blur = cv2.GaussianBlur(gray, (5, 5), 0)
    # Apply thresholding to segment the image
    ret, thresh = cv2.threshold(blur, 0, 255, cv2.THRESH_BINARY+cv2.THRESH_OTSU)

    # Find contours in the binary image
    contours, hierarchy = cv2.findContours(thresh, cv2.RETR_TREE, cv2.CHAIN_APPROX_SIMPLE)

    # Select the contour with the largest area (i.e., the pleural boundary)
    contour_sizes = [(cv2.contourArea(contour), contour) for contour in contours]
    largest_contour = max(contour_sizes, key=lambda x: x[0])[1]

    # Extract features from the pleural boundary
    perimeter = cv2.arcLength(largest_contour, True)
    area = cv2.contourArea(largest_contour)
    circularity = (4 * np.pi * area) / (perimeter ** 2)

    # Extract additional features
    rect = cv2.minAreaRect(largest_contour)
    rect_area = rect[1][0] * rect[1][1]
    aspect_ratio = rect[1][0] / rect[1][1]
    extent = area / rect_area
    solidity = area / cv2.contourArea(cv2.convexHull(largest_contour))

   # Extract features from the vessel segments


# find the GLCM features
    # Convert float image to unsigned integer type
    #image_gray = rgb2gray(img)
    image_gray_uint = (gray * 255).astype(np.uint8)

    # Define GLCM properties
    distances = [1, 2, 3]
    angles = [0, np.pi/4, np.pi/2, 3*np.pi/4]

    # Compute GLCM features
    glcm = feature.greycomatrix(image_gray_uint, distances, angles, levels=256, symmetric=True, normed=True)
    contrast = feature.greycoprops(glcm, 'contrast')
    dissimilarity = feature.greycoprops(glcm, 'dissimilarity')
    homogeneity = feature.greycoprops(glcm, 'homogeneity')
    energy = feature.greycoprops(glcm, 'energy')
    correlation = feature.greycoprops(glcm, 'correlation')


    # Define GLRLM properties
    distances = [1, 2, 3]
    angles = [0, np.pi/4, np.pi/2, 3*np.pi/4]

    # Compute GLRLM features3
    glrlm = feature.greycomatrix(image_gray_uint, distances, angles, levels=256, symmetric=False, normed=True)


   # find the Density Features

    mean_density = np.mean(img)
    std_density = np.std(img)


    # Compute the voxel size of the image
    voxel_size = [0.1, 0.1, 0.1]  # example voxel size in mm

    # Convert the image and mask to float32 arrays
    image_array = np.float32(img)
    #mask_array = np.float32(mask)

    # Compute the lung volume using the mask and voxel size
    lung_mask = image_array > 0
    #lung_tissue = image_array[lung_mask]
    lung_volume = np.sum(lung_mask) * voxel_size[0] * voxel_size[1] * voxel_size[2] * np.mean(lung_mask)


    # Convert the image to grayscale
    #image_gray = color.rgb2gray(img)

    # Define the LBP properties
    radius = 3
    n_points = 8 * radius
    method = 'uniform'

    # Compute the LBP image and extract the features
    lbp = local_binary_pattern(gray, n_points, radius, method)
    hist, _ = np.histogram(lbp.ravel(), bins=np.arange(0, n_points + 3), range=(0, n_points + 2))
    hist = hist.astype('float')
    hist /= (hist.sum() + 1e-7)
    uniformity = np.power(hist, 2).sum()




#wb ratio

    df1.loc[j]=({'Class':c, 'Perimeter':perimeter, 'Area':area, 'Circularity':circularity, 'Aspect Ratio':aspect_ratio,'Extent':extent,
                 'Solidity':solidity,'Rect_area':rect_area,'contrast':np.mean(contrast),
                 'dissimilarity':np.mean(dissimilarity),'homogeneity':np.mean(homogeneity),'energy':np.mean(energy),
                 'correlation':np.mean(correlation),
                 'glrlm':np.mean(glrlm),'mean_density':mean_density,'std_density':std_density,
                 'lung_volume':lung_volume,'hist':np.mean(hist),'uniformity':np.mean(uniformity)})
    j+=1


frames = df1


############################################### give directy to save csv file
frames.to_csv(csv,index=False)### give train.csv path

###############################################################################

working on img  Pneumonia__ (2876).png


/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:35: skimage_deprecation: Function ``greycomatrix`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycomatrix`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/fea

working on img  Pneumonia__ (2877).png


/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:35: skimage_deprecation: Function ``greycomatrix`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycomatrix`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/fea

working on img  Pneumonia__ (2878).png


...

/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:35: skimage_deprecation: Function ``greycomatrix`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycomatrix`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/fea

working on img  Pneumonia__ (874).png


/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:35: skimage_deprecation: Function ``greycomatrix`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycomatrix`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/fea

working on img  Pneumonia__ (875).png


/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:35: skimage_deprecation: Function ``greycomatrix`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycomatrix`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/feature/__init__.py:42: skimage_deprecation: Function ``greycoprops`` is deprecated and will be removed in version 1.0. Use ``skimage.feature.graycoprops`` instead.
  removed_version='1.0')
/usr/local/lib/python3.9/dist-packages/skimage/fea